In [1]:
import tensorflow as tf
from tensorflow.contrib import layers
from tensorflow.contrib import rnn  # rnn stuff temporarily in contrib, moving back to code in TF 1.1
import os
import time
import math
import numpy as np
import pandas as pd
import my_txtutils as txt

In [2]:
#
SEQLEN = 30
BATCHSIZE = 200
ALPHASIZE = txt.ALPHASIZE
INTERNALSIZE = 512
NLAYERS = 3
learning_rate = 0.001  # fixed learning rate
dropout_pkeep = 0.4    # some dropout

In [3]:
#data = open('tiny-shakespeare.txt', 'r').read() # should be simple plain text file
#chars = list(set(data))
#data_size, vocab_size = len(data), len(chars)
codetext, valitext, bookranges = txt.read_data_files('tensorflow-rnn-shakespeare-master/shakespeare/*.txt', validation=True)

# display some stats on the data
epoch_size = len(codetext) // (BATCHSIZE * SEQLEN)

Loading file tensorflow-rnn-shakespeare-master/shakespeare/1kinghenryiv.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/1kinghenryvi.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/2kinghenryiv.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/2kinghenryvi.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/3kinghenryvi.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/allswellthatendswell.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/antonyandcleopatra.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/asyoulikeit.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/comedyoferrors.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/coriolanus.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/cymbeline.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/hamlet.txt
Loading file tensorflow-rnn-shakespeare-master/shakespeare/juliuscaesar.txt
Loading 

In [4]:

lr = tf.placeholder(tf.float32, name='lr')  # learning rate
pkeep = tf.placeholder(tf.float32, name='pkeep')  # dropout parameter
batchsize = tf.placeholder(tf.int32, name='batchsize')

In [5]:
# inputs
X = tf.placeholder(tf.uint8, [None, None], name='X')    # [ BATCHSIZE, SEQLEN ]
Xo = tf.one_hot(X, ALPHASIZE, 1.0, 0.0)                 # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# expected outputs = same sequence shifted by 1 since we are trying to predict the next character
Y_ = tf.placeholder(tf.uint8, [None, None], name='Y_')  # [ BATCHSIZE, SEQLEN ]
Yo_ = tf.one_hot(Y_, ALPHASIZE, 1.0, 0.0)               # [ BATCHSIZE, SEQLEN, ALPHASIZE ]
# input state
Hin = tf.placeholder(tf.float32, [None, INTERNALSIZE*NLAYERS], name='Hin')  # [ BATCHSIZE, INTERNALSIZE * NLAYERS]

In [6]:
# How to properly apply dropout in RNNs: see README.md
cells = [rnn.GRUCell(INTERNALSIZE) for _ in range(NLAYERS)]
# "naive dropout" implementation
dropcells = [rnn.DropoutWrapper(cell,input_keep_prob=pkeep) for cell in cells]
multicell = rnn.MultiRNNCell(cells, state_is_tuple=False)
multicell = rnn.DropoutWrapper(multicell, output_keep_prob=pkeep) 

In [7]:

Yr, H = tf.nn.dynamic_rnn(multicell, Xo, dtype=tf.float32, initial_state=Hin)
# Yr: [ BATCHSIZE, SEQLEN, INTERNALSIZE ] -- output
# H:  [ BATCHSIZE, INTERNALSIZE*NLAYERS ] # this is the last state in the sequence -- final state

In [8]:

H = tf.identity(H, name='H')  # just to give it a name

In [9]:
Yflat = tf.reshape(Yr, [-1, INTERNALSIZE])    # [ BATCHSIZE x SEQLEN, INTERNALSIZE ]
Ylogits = layers.linear(Yflat, ALPHASIZE)     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Yflat_ = tf.reshape(Yo_, [-1, ALPHASIZE])     # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
loss = tf.nn.softmax_cross_entropy_with_logits(logits=Ylogits, labels=Yflat_)  # [ BATCHSIZE x SEQLEN ]
loss = tf.reshape(loss, [batchsize, -1])      # [ BATCHSIZE, SEQLEN ]
Yo = tf.nn.softmax(Ylogits, name='Yo')        # [ BATCHSIZE x SEQLEN, ALPHASIZE ]
Y = tf.argmax(Yo, 1)                          # [ BATCHSIZE x SEQLEN ]
Y = tf.reshape(Y, [batchsize, -1], name="Y")  # [ BATCHSIZE, SEQLEN ]
train_step = tf.train.AdamOptimizer(lr).minimize(loss)

In [10]:
# init
istate = np.zeros([BATCHSIZE, INTERNALSIZE*NLAYERS])  # initial zero input state
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
step = 0
# stats for display
seqloss = tf.reduce_mean(loss, 1)
batchloss = tf.reduce_mean(seqloss)
accuracy = tf.reduce_mean(tf.cast(tf.equal(Y_, tf.cast(Y, tf.uint8)), tf.float32))
loss_summary = tf.summary.scalar("batch_loss", batchloss)
acc_summary = tf.summary.scalar("batch_accuracy", accuracy)
summaries = tf.summary.merge([loss_summary, acc_summary])
timestamp = str(math.trunc(time.time()))
summary_writer = tf.summary.FileWriter("log/" + timestamp + "-training")
validation_writer = tf.summary.FileWriter("log/" + timestamp + "-validation")

In [11]:

# Init for saving models. They will be saved into a directory named 'checkpoints'.
# Only the last checkpoint is kept.
if not os.path.exists("checkpoints"):
    os.mkdir("checkpoints")
saver = tf.train.Saver(max_to_keep=1000)
# for display: init the progress bar
DISPLAY_FREQ = 50
_50_BATCHES = DISPLAY_FREQ * BATCHSIZE * SEQLEN
# training loop
for x, y_, epoch in txt.rnn_minibatch_sequencer(codetext, BATCHSIZE, SEQLEN, nb_epochs=10):

    # train on one minibatch
    feed_dict = {X: x, Y_: y_, Hin: istate, lr: learning_rate, pkeep: dropout_pkeep, batchsize: BATCHSIZE}
    _, y, ostate = sess.run([train_step, Y, H], feed_dict=feed_dict)

    # log training data for Tensorboard display a mini-batch of sequences (every 50 batches)
    if step % _50_BATCHES == 0:
        feed_dict = {X: x, Y_: y_, Hin: istate, pkeep: 1.0, batchsize: BATCHSIZE}  # no dropout for validation
        y, l, bl, acc, smm = sess.run([Y, seqloss, batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_learning_learned_comparison(x, y, l, bookranges, bl, acc, epoch_size, step, epoch)
        summary_writer.add_summary(smm, step)

    if step // 3 % _50_BATCHES == 0:
        txt.print_text_generation_header()
        ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
        rh = np.zeros([1, INTERNALSIZE * NLAYERS])
        for k in range(1000):
            ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
            rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
            print(chr(txt.convert_to_alphabet(rc)), end="")
            ry = np.array([[rc]])
        txt.print_text_generation_footer()
        
    if step // 10 % _50_BATCHES == 0:
        saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)
        print("Saved file: " + saved_file)

    
    # loop state around
    istate = ostate
    step += BATCHSIZE * SEQLEN



   0 (epoch 0) 1kinghenryiv.txt │  1 KING HENRY IV\\\ DRAMATIS P │       eeeeeee                  │ loss: 4.55972
  30 (epoch 0) 1kinghenryiv.txt │ here,\ But not the form of wha │                                │ loss: 4.47455
  60 (epoch 0) 1kinghenryiv.txt │ l cowards!\ Give me a cup of s │                                │ loss: 4.50351
  90 (epoch 0) 1kinghenryiv.txt │ d.\\HOTSPUR Will not you?\\GLE │                                │ loss: 4.55537
 120 (epoch 0) 1kinghenryiv.txt │  he is grievous sick.\\HOTSPUR │                                │ loss: 4.53265
 150 (epoch 0) 1kinghenryiv.txt │  stepp'd forth before the king │                                │ loss: 4.47362
 180 (epoch 0) 1kinghenryiv.txt │  Scales with him and Lord Hung │                                │ loss: 4.48817
 210 (epoch 0) 1kinghenryiv.txt │  of a warlike enterprise\ More │                                │ loss: 4.46922
 240 (epoch 0) 1kinghenryiv.txt │ ve their giddy brains knock'd  │                     

toe stCgeCghCgCne

teesCnCn neh t nogsho o  ho
e 
o ht

shttg 
ee stge net
tCngeg nntthh sohnehCC 
ohs
sgs eo  hssg ehhhnthgs nhnhgt Cgt
 nnhe
nhoegeesss
hstteCeoCet tn soCottoo
nn
gostothtCohsCnhenno
oeIesC 
soso
oICt 
Co
ItsI
 oh
beho
Ceste I
 eChntnog  nCsh ChhgnnCnet s
gsg
hCnoonne   hhetssgoh  
Ct s

gotCg C 
ego
hget CeCtg
nh nheg
thsoCCgtCg h  tsnsCohonoCgeooo 
ooChotIChI eyC Conh C eosC nCsg
tsssh gC
eoI  tsCtgggg gootthgC CCogCsohenteehsgesh
hnseehg
oso sCI ot
 g e tntehtheeoCh

ogeso gno esC



tono sht h  gnCeehnnhtentCsgeeoshhnC 
thCh
goCshgeht ett n ogotC tCghtote

 estn 
ggCnetCeon eth
sg
gC
go
g

h
gohhssgsbsnngy yIsetg
tgog sg engennsCtt
gCtosoeeoC hosssCngnntC tnsht oonthoeegooshtetoC
 ngC
gnCesCos
hohICghone non CChIoen sCt
ne
 nnennsns
 t gggCg
ghCttC
o set
nttehnognntsCtnoetCo eh

tCee eeehoghgh esgtesn
onntosCtCo
sC ssnn Chtohh ttn hhyt 
 sooC snnhegegnh
snosog gCt CCsgt sonCoen

tC s neotn s
hCn hnC h
esoCsosnssn 
└───────────────────────────────────────────────En


600000 (epoch 0) 3kinghenryvi.txt │ en of Herefordshire to fight\  │   oe o         te  te eee   \h │ loss: 3.00119
600030 (epoch 0) 3kinghenryvi.txt │ l it: upon my life, it will do │  oe   oe  te ooe   ho eee  te  │ loss: 2.77393
600060 (epoch 0) 3kinghenryvi.txt │ PRINCE HENRY What, fought you  │ AE    I            oe    ee  o │ loss: 3.03060
600090 (epoch 0) 3kinghenryvi.txt │ , opinion and disdain:\ The le │  ooee    to  tee   e \\Ihe te  │ loss: 2.63875
600120 (epoch 0) 3kinghenryvi.txt │ art can think: there is not su │    ooe eee   \hoe   oe ee  hee │ loss: 2.68404
600150 (epoch 0) 3kinghenryvi.txt │ r to-day hath bought\ Thy like │  tee  t ooe  eee    \hhe toe   │ loss: 3.02658
600180 (epoch 0) 3kinghenryvi.txt │ r hungry prey.\\ALENCON Froiss │  oee    ooe  \\ II     I       │ loss: 2.96382
600210 (epoch 0) 3kinghenryvi.txt │ ny of his false confederates.\ │   to eee tee   ooe      e   \\ │ loss: 2.68936
600240 (epoch 0) 3kinghenryvi.txt │ s no more;\ But join in friend │  t


900000 (epoch 0) antonyandcleopatra.txt │ th:\ And is not this an honour │  e\ Tn  tn tot ahen sndter     │ loss: 2.20759
900030 (epoch 0) antonyandcleopatra.txt │ ur horse not packed. What, ost │   ter   ton aone s \Ioet  tn   │ loss: 2.57035
900060 (epoch 0) antonyandcleopatra.txt │ even of\ the eleven I paid.\\P │  e stn  The toe e  t tott \\ A │ loss: 2.41194
900090 (epoch 0) antonyandcleopatra.txt │  on the wanton rushes lay you  │ tn the tond   tot e  ton tor t │ loss: 2.26355
900120 (epoch 0) antonyandcleopatra.txt │  Mars shall on his altar sit\  │ tone toen  tn ten tnt netonh T │ loss: 2.48686
900150 (epoch 0) antonyandcleopatra.txt │ pered: there's\ not three of m │ ere  \the   s  Tnd thee  tn te │ loss: 2.18975
900180 (epoch 0) antonyandcleopatra.txt │ Exit BASTARD OF ORLEANS]\\ But │ ott     I   INSINSSS      AEn  │ loss: 2.85147
900210 (epoch 0) antonyandcleopatra.txt │ ours bear me company?\\BEDFORD │     to t te toreend\\  ARA     │ loss: 2.66281
900240 (epoch 0) antony

LATE	Ans I I	ou h tres otis,

	Iod, be torunsd
	Ontes, sansise thand, ol hasl, mar wifd and,
	Wuat thy that isd in there soacis trine
	The tirteed.

BARU	UI O Wrhu lse to thith s autl tat in wadt oon helses.
	Tsute more srurls

	I the taud ate by ore wode, did torlerese.
	Hon mher irild
	Sn me lul ort or orr caus.

SSE	ARRSASUIS	Oee nist hee bfenl sand sin saude.
	I dle tood bitor oind we tin thels,
	Bririer, ther thad dend onr sinchor.

	Onds ind thor

	[Ale mh t rer wars mine d oaus tord
	Wo saterin tiud teonrtit
	Anris sans an he os the wnd lo me thor:
	Hud druad bheut and
	Onor mon anthee feas therd.	In it an mils
	Ior dot ait as coos lhel mure,


SOESNA	S oad, yen hat shand saterne,
	To tho merager, me sas there, I	sl in whee,
	Thhe tonugha me teit,
	Aat mure the an hr fee atin
	I lirl, af som wt onun londee the tonn bod.

	EE CLO	Tead, the ce tous tos fhres oise
	Hel hronged thice tons hon,
	Thil sh see, wo to wod senld wosd,

	An o
└──────────────────────────────────────────────

...


50400000 (epoch 9) sonnets.txt │ lbot's ghost,\ He speaks with  │ bot's soost.\ Ae wheaks tith t │ loss: 0.79697
50400030 (epoch 9) sonnets.txt │ she.\\KING HENRY VI Whether it │ tae\\CING HENRY VI Iharher tn  │ loss: 0.77540
50400060 (epoch 9) sonnets.txt │  as it is: I were better to be │ tn tt is. t wire aester th se  │ loss: 1.15886
50400090 (epoch 9) sonnets.txt │ f war\ In disadvantage; to abi │  har, Tn tescsmantage  ah t od │ loss: 1.43405
50400120 (epoch 9) sonnets.txt │ ENCE Indeed, sir, to my cost.\ │ NCE A deed, tir, th ty lout \\ │ loss: 0.85567
50400150 (epoch 9) sonnets.txt │ heering a rout of rebels with  │ aer ng t fiunlof seaels,tith t │ loss: 1.29657
50400180 (epoch 9) sonnets.txt │ re you with grief had spoke an │ e tou sith mraef aav seoke tnd │ loss: 0.89033
50400210 (epoch 9) sonnets.txt │ g dream'd of such a kind of ma │  teoad'd tn tuch a sing of sen │ loss: 1.08477
50400240 (epoch 9) sonnets.txt │ lk, let them go.\\ALL Come, le │ k, set mhem bo.\\ NB Tome, ce

	With all my house and this did stand on this.

	[Exit]




	THE TAMING OF THE SHREW


ACT III



SCENE I	The same. The French camp. The Poins of Armado's house.


	[Flourish. Enter KING HENRY V and BASSANIO]

GRUMIO	What say you?

LUCETTA	Ay, my lord.

CARDINAL WOLSEY	The senators
	Are this the father that they say is to be theirs.

CASSIO	The god sent for the money!

BENEDICK	They are now at a body of torner than the time.

CLEOPATRA	What says the man?

BENEDICK	They are the first thing that they are come
	To the sea and trumpet to the sea.

SIR HUGH EVANS	It is the field, the devil's death is this.

ANTONIO	What is the third to the sun?

APEMANTUS	To the sea,
	To the man in her chamber and the fair despite
	Of my dispose the more than the sea-side of the wars
	That thou hast struck me to the sea of friends.
	The sun that loves me welcome with me.
	I would the world is thine that thou hast stay'd at me.

KING HENRY V	I am the sun that shall be the strong course of thee
	And the d
└──


51000000 (epoch 9) troilusandcressida.txt │ ould be deliver'd to his holin │ uld be tesiver'd to tis horine │ loss: 0.64967
51000030 (epoch 9) troilusandcressida.txt │ , still unfold\ The acts comme │  ttall tntold\ The dct  ooneen │ loss: 1.16051
51000060 (epoch 9) troilusandcressida.txt │ ing himself in project of a po │ ng tim elf an trioect of t sao │ loss: 1.02703
51000090 (epoch 9) troilusandcressida.txt │ rfumes the blood ere one can s │ comes yhe deood one yf  won da │ loss: 1.22104
51000120 (epoch 9) troilusandcressida.txt │  be a\ soldier-like word, and  │ te\a  gordier,bike tird. and t │ loss: 1.07445
51000150 (epoch 9) troilusandcressida.txt │ STMORELAND I pledge your grace │ TMORELAND T wraage tour grace  │ loss: 0.82947
51000180 (epoch 9) troilusandcressida.txt │  Holy Land,\ Lest rest and lyi │ wely Pond\\ Aett teso and doin │ loss: 1.47087
51000210 (epoch 9) troilusandcressida.txt │  pardons. If you look\ for a g │ sardon,,\W  you wovk\ tor y po │ loss: 1.17108
5100024

Saved file: checkpoints/rnn_train_1499353120-51000000

51300000 (epoch 9) various.txt │ .\ Command the conquest, Charl │ \\Tomeend the mousuest  taarle │ loss: 1.07641
51300030 (epoch 9) various.txt │ ongues\ They bring smooth comf │ ngues, Wha  seeng toetth tompo │ loss: 1.17804
51300060 (epoch 9) various.txt │ e still-born, and that we now  │  aorll -orne tnd thet te sew s │ loss: 1.30919
51300090 (epoch 9) various.txt │ weaker vessel, as they say, th │ oarer tersel, an yhe  say, the │ loss: 0.94129
51300120 (epoch 9) various.txt │ aith,\ well said, Sir John, ve │ ith,  Ih l ihid  sir Tohn, yer │ loss: 1.03458
51300150 (epoch 9) various.txt │ ill not go off until they hear │ tl yot bo fnf tntol the  aaard │ loss: 1.02776
51300180 (epoch 9) various.txt │  IV\\\ACT V\\\\SCENE I Glouces │ IV\\\ACT I\\\\SCENE IIAloucest │ loss: 0.37150
51300210 (epoch 9) various.txt │ good night: and so kneel down\ │ ood tight. Ind yo tiowl yown   │ loss: 0.94207
51300240 (epoch 9) various.txt │ spect is

BIRON	And what a devil should thy face be wither'd with a false?
	The sun we meet to thee, that thou wilt find
	A thousand will to stand unto the fall,
	As if thou weep'd it as thy spirits are as sharp shall see,
	To change the fearful times to change thee thine.
	But what a man is this the fool hath stirred them?
	Why, there's a fall, the world is set on him.

	[Exit]

	[Enter OTHELLO and LUCILIUS with a love and stand at the stage]

SIR TOBY BELCH	Then you are so believed and to the course.

DON PEDRO	That was the more than the fourth world,
	The pretty thing it with the fair desires that say so.

	[Enter ANTIOCHUS and CLEON]

	[Re-enter OCTAVIUS CAESAR, AGRIPPA and
	Attendants]

ANTIPHOLUS
OF EPHESUS	I think, the world is changed the world.

CASSIUS	What, will you go?
	Why, then, there is no matter. What is your father's deet?
	Well may be sent to say 'God should be seen a secret fortune,
	Which is not thinking on his head and say
	The winted
└───────────────────────────────────────

In [12]:
saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)

In [13]:
print("saved file" + saved_file)

saved filecheckpoints/rnn_train_1499353120-51360000
